<a href="https://colab.research.google.com/github/paulowiz/uff_engenharia_de_dados_com_python/blob/master/uff_engenharia_de_dados_com_python.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Setup Google Colab


In [122]:
from google.colab import data_table
from vega_datasets import data

data_table.enable_dataframe_formatter()

# use seu data.seudataframe() para mostrar bunito

# Tutorial pratico ETL (Extraction,Transformation,Loading)

## PT - Extração,Transformação e Carregamento de dados 


### Problema a ser resolvido:

O escritório de inovação de uma empresa precisa de um engenheiro de dados para fazer uma nova "Pipeline de Dados" para que eles possam ter acesso aos novos arquivos sobre patentes do setor publico de patentes dos Estados Unidos da America(USPTO).Com esses dados eles poderão fazer o download com o link facilidade e verificar quantos arquivos são processados diariamente. 

# Extração de dados 

É o processo que analisa o provedor de dados, os tipos de dados que serão processados e faz a conexão com esse provedor através de REST API, Web Scrapping, SOAP etc. 

Em nosso caso, como nosso provider é o USPTO, não temos uma API deles para consumir esses dados.... então vamos utilizar a técnica de raspagem da web(Web Scrapping) que vamos pegar os dados direto do website. 

In [123]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from sqlalchemy import create_engine
import pandas as pd
from tqdm import tqdm

class Uspto:
    """Classe que extrai os dados sobre arquivos de patentes do USPTO"""

    def __init__(self, year):
        """
        Construtor que pega o ano como referência para iniciar a extração.
        """
        try:
            self.year = int(year)
        except:
            print('Year must be a number')
            return False
        self.link = 'https://bulkdata.uspto.gov/data/patent/application/redbook/fulltext/' + str(year) + '/'

    def get_uspto_files_information(self):
        headers = {
            "User-Agent":
                "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/70.0.3538.102 Safari/537.36 Edge/18.19582"
        }

        page = requests.get(self.link, headers=headers)

        soup = BeautifulSoup(page.text, 'html.parser')

        soup = soup.find_all('table')
        soup = soup[-1]
        arr_files =[]
        trs = soup.find_all('tr')
        for tr in trs:
            tds = tr.find_all('td')
            dict_temp = {}
            try:
                dict_temp = {'filename': tds[0].text, 'size': tds[1].text, 'publish_on': tds[2].text, 'url': self.link+tds[0].find('a')['href']}
                arr_files.append(dict_temp)
            except:
                continue

        return arr_files

    def transform_and_load(self,files):
            df = pd.DataFrame(files)
            df.head(10)
            engine = create_engine('sqlite:///patent.db', echo=False)
            df.to_sql('uspto_files', con=engine, if_exists='append')

pass

### Chamando a classe de extração que criamos acima 

In [124]:
for year in tqdm(range(2010,2022)):
    uspto = Uspto(year)
    files = uspto.get_uspto_files_information()
    uspto.transform_and_load(files)
print(files[0])

100%|██████████| 12/12 [00:06<00:00,  1.90it/s]

{'filename': 'ipa210107.zip', 'size': '147841751', 'publish_on': '2021-01-07 00:01', 'url': 'https://bulkdata.uspto.gov/data/patent/application/redbook/fulltext/2021/ipa210107.zip'}


# Importando o pandas e inserindo os dados coletados no dataframe

In [125]:
df = pd.DataFrame(files)
df.head(10)

filename       size        publish_on  \
0  ipa210107.zip  147841751  2021-01-07 00:01   
1  ipa210114.zip  156042926  2021-01-14 00:01   
2  ipa210121.zip  146902825  2021-01-21 00:01   
3  ipa210128.zip  154837377  2021-01-28 00:01   
4  ipa210204.zip  154202636  2021-02-04 00:01   
5  ipa210211.zip  155928214  2021-02-11 00:01   
6  ipa210218.zip  136650642  2021-02-18 00:01   
7  ipa210225.zip  148148145  2021-02-25 00:01   
8  ipa210304.zip  176522001  2021-03-04 00:01   
9  ipa210311.zip  171245107  2021-03-11 00:02   

                                                 url  
0  https://bulkdata.uspto.gov/data/patent/applica...  
1  https://bulkdata.uspto.gov/data/patent/applica...  
2  https://bulkdata.uspto.gov/data/patent/applica...  
3  https://bulkdata.uspto.gov/data/patent/applica...  
4  https://bulkdata.uspto.gov/data/patent/applica...  
5  https://bulkdata.uspto.gov/data/patent/applica...  
6  https://bulkdata.uspto.gov/data/patent/applica...  
7  https://bulkdata.uspto.gov/data/patent/applica...  
8  https://bulkdata.uspto.gov/data/patent/applica...  
9  https://bulkdata.uspto.gov/data/patent/applica...

### Fazendo o Load dos ddados no Sqlite

In [126]:
engine = create_engine('sqlite:///patent.db', echo=False)
df.to_sql('uspto_files', con=engine, if_exists='append')

In [127]:
df['url'][0]

'https://bulkdata.uspto.gov/data/patent/application/redbook/fulltext/2021/ipa210107.zip'

In [128]:
!wget https://bulkdata.uspto.gov/data/patent/application/redbook/fulltext/2022/ipa220106.zip

--2022-10-17 18:36:29--  https://bulkdata.uspto.gov/data/patent/application/redbook/fulltext/2022/ipa220106.zip
Resolving bulkdata.uspto.gov (bulkdata.uspto.gov)... 151.207.240.28, 2610:20:5004:1604::28
Connecting to bulkdata.uspto.gov (bulkdata.uspto.gov)|151.207.240.28|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 163074754 (156M) [application/zip]
Saving to: ‘ipa220106.zip’

ipa220106.zip       100%[===================>] 155.52M  4.19MB/s    in 37s     

2022-10-17 18:37:06 (4.20 MB/s) - ‘ipa220106.zip’ saved [163074754/163074754]



In [129]:
!unzip ipa220106.zip

Archive:  ipa220106.zip
  inflating: ipa220106.xml           


In [130]:
!mkdir xml-patents
!cd xml-patents && mkdir ipa220106

mkdir: cannot create directory ‘xml-patents’: File exists
mkdir: cannot create directory ‘ipa220106’: File exists


In [131]:
!csplit -s -f 'xml-patents/ipa220106/ipa220106-' -b '%02d.xml' ipa220106.xml '/^<?xml /' '{*}'

## Transformação dos dados

### Clean Functions

In [132]:
import re
from datetime import datetime 
import pandas as pd 
import xml.etree.ElementTree as et 
import tqdm
import glob


def dateint_to_date(dateint):
    # you could also import date instead of datetime and use that.
    date = datetime(year=int(dateint[0:4]), month=int(dateint[4:6]), day=int(dateint[6:8]))
    return date.strftime("%Y-%m-%d")

def convert_xml_folder_to_dataframe(xnl_folder_path):
  pbar = tqdm.tqdm(glob.iglob(xnl_folder_path + '/*.xml'))
  rows = []
  logs = []
  df_cols = ["doc_number", "file","invention_title", "abstract", "published_date","country"]
  df_logs_cols = ["path","obs"]
  for filepath in pbar:
     try:
        xtree = et.parse(filepath)
        # Pega a tag principal do XML
        xroot = xtree.getroot() 
        # Pega as informações principais da patente
        main_patent_info = xroot.attrib
        data_application = xroot.find('us-bibliographic-data-application')
        # Pega o titulo da invenção 
        try:
          invention_title = data_application.find('invention-title').text
        except:
          pass
        # Pega o abstract (Descrição curta da invenção)
        abstract = xroot.find('abstract')
        abstract_paragraphs = abstract.findall('p')
        full_abstract = ''
        for abstract_p in abstract_paragraphs:
            full_abstract = full_abstract + abstract_p.text
        # Aproveita o array dos atributos da invenção e salva o abstract e o titulo la também 
        rows.append({
                'doc_number':main_patent_info['file'].split('.')[0],
                'file':main_patent_info['file'],
              'invention_title': invention_title,
              'abstract':full_abstract, 
              'published_date': main_patent_info['date-publ'],
              'country':main_patent_info['country']})
     except:
         logs.append({'path': filepath,'obs':'Erro ao processar o arquivo!'})

  out_df = pd.DataFrame(rows, columns = df_cols)
  out_df_logs = pd.DataFrame(logs, columns = df_logs_cols)
  out_df_logs.to_csv('logs_error.csv')
  return out_df

In [133]:
df_limpo = convert_xml_folder_to_dataframe('/content/xml-patents/ipa220106')

    


7883it [00:32, 242.28it/s]


In [134]:
display(df_limpo)

doc_number                          file  \
0     US20220003366A1-20220106  US20220003366A1-20220106.XML   
1     US20220002323A1-20220106  US20220002323A1-20220106.XML   
2     US20220001642A1-20220106  US20220001642A1-20220106.XML   
3     US20220006529A1-20220106  US20220006529A1-20220106.XML   
4     US20220004790A1-20220106  US20220004790A1-20220106.XML   
...                        ...                           ...   
7457  US20220004284A1-20220106  US20220004284A1-20220106.XML   
7458  US20220000213A1-20220106  US20220000213A1-20220106.XML   
7459  US20220003213A1-20220106  US20220003213A1-20220106.XML   
7460  US20220005857A1-20220106  US20220005857A1-20220106.XML   
7461  US20220004917A1-20220106  US20220004917A1-20220106.XML   

                                        invention_title  \
0     DIVIDABLE LED BAR AND LED LIGHTING DEVICE INCL...   
1             PROCESS FOR PREPARING ORGANOTIN COMPOUNDS   
2             ENCAPSULATED FRAGILE INSULATION MATERIALS   
3     CONTROL APPARATUS, CONNECTION STATUS REGISTRAT...   
4       DRIVER MONITOR AND METHOD FOR MONITORING DRIVER   
...                                                 ...   
7457                                 CHANNEL SCAN LOGIC   
7458            FOOTPLATE DEVICE FOR VIBRATING FOOTWEAR   
7459  Unmanned Aerial Vehicle Wind Turbine Inspectio...   
7460  TAPELESS LEADFRAME PACKAGE WITH EXPOSED INTEGR...   
7461  BENCHMARKING DECISION MAKING UNITS USING DATA ...   

                                               abstract published_date country  
0     The present invention relates to an LED lighti...       20220106      US  
1     Provided is an efficient and effective process...       20220106      US  
2     A composite board comprising (i) a first foam ...       20220106      US  
3     A control apparatus for registering a connecti...       20220106      US  
4     A driver monitor includes a processor configur...       20220106      US  
...                                                 ...            ...     ...  
7457  A device that can autonomously scan a sensor p...       20220106      US  
7458  Embodiments include a footplate device for pla...       20220106      US  
7459  Methods, systems and apparatus, including comp...       20220106      US  
7460  A first side of a tapeless leadframe package i...       20220106      US  
7461  In an example embodiment, a recommendation eng...       20220106      US  

[7462 rows x 6 columns]

In [135]:
df_limpo.shape

(7462, 6)

In [136]:
df_logs = pd.read_csv('logs_error.csv')
display(df_logs)

Unnamed: 0                                               path  \
0             0  /content/xml-patents/ipa220106/ipa220106-2918.xml   
1             1  /content/xml-patents/ipa220106/ipa220106-3043.xml   
2             2  /content/xml-patents/ipa220106/ipa220106-2537.xml   
3             3  /content/xml-patents/ipa220106/ipa220106-2375.xml   
4             4  /content/xml-patents/ipa220106/ipa220106-2400.xml   
..          ...                                                ...   
416         416  /content/xml-patents/ipa220106/ipa220106-3115.xml   
417         417  /content/xml-patents/ipa220106/ipa220106-2891.xml   
418         418  /content/xml-patents/ipa220106/ipa220106-2459.xml   
419         419  /content/xml-patents/ipa220106/ipa220106-2351.xml   
420         420  /content/xml-patents/ipa220106/ipa220106-2589.xml   

                              obs  
0    Erro ao processar o arquivo!  
1    Erro ao processar o arquivo!  
2    Erro ao processar o arquivo!  
3    Erro ao processar o arquivo!  
4    Erro ao processar o arquivo!  
..                            ...  
416  Erro ao processar o arquivo!  
417  Erro ao processar o arquivo!  
418  Erro ao processar o arquivo!  
419  Erro ao processar o arquivo!  
420  Erro ao processar o arquivo!  

[421 rows x 3 columns]

In [137]:
df_logs.shape

(421, 3)

## Load dados limpos 

In [138]:
from sqlalchemy import create_engine
import pandas as pd

engine = create_engine('sqlite:///patent.db', echo=False)
df_limpo.to_sql('patent', con=engine, if_exists='append')